In [18]:
import os
import numpy as np
import pandas as pd
import pickle
import quandl
from datetime import datetime
import plotly.offline as py
import plotly.graph_objs as go
import plotly.figure_factory as ff
py.init_notebook_mode(connected=True)

def get_quandl_data(quandl_id):
    '''Download and cache Quandl dataseries. Use pickle to serialise & 
    save data as file which will prevent script from re-downloading 
    same data each time script is run'''
    cache_path = '{}.pk'.format(quandl_id).replace('/','-')
    try:
        f = open(cache_path,'rb') #read bytes
        df = pickle.load(f) #load pickled data in order to read as dataframe
        print('Loaded {} from cache. '.format(quandl_id))
    except (OSError, IOError) as e:
        print('Downloading {} from Quandl.'.format(quandl_id))
        df = quandl.get(quandl_id,returns='pandas') #retrieve bitcoin currency as per input path and return as pandas dataframe
        df.to_pickle(cache_path) #convert dataframe to pickle object
        print('Cached {} at {}'.format(quandl_id,cache_path))
    return df

#All Bitcoin codes follow the same format: BCHARTS/{MARKET}{CURRENCY}
#pull Kraken BTC price exchange data
btc_usd_price_kraken = get_quandl_data('BCHARTS/KRAKENUSD')


Loaded BCHARTS/KRAKENUSD from cache. 


In [19]:
btc_usd_price_kraken.head()

Open       High        Low      Close  Volume (BTC)  \
Date                                                                   
2014-01-07  874.67040  892.06753  810.00000  810.00000     15.622378   
2014-01-08  810.00000  899.84281  788.00000  824.98287     19.182756   
2014-01-09  825.56345  870.00000  807.42084  841.86934      8.158335   
2014-01-10  839.99000  857.34056  817.00000  857.33056      8.024510   
2014-01-11  858.20000  918.05471  857.16554  899.84105     18.748285   

            Volume (Currency)  Weighted Price  
Date                                           
2014-01-07       13151.472844      841.835522  
2014-01-08       16097.329584      839.156269  
2014-01-09        6784.249982      831.572913  
2014-01-10        6780.220188      844.938794  
2014-01-11       16698.566929      890.671709

In [20]:
#chart the BTC pricing data as quick visual verification
btc_trace = go.Scatter(x=btc_usd_price_kraken.index,y=btc_usd_price_kraken['Weighted Price'])
py.iplot([btc_trace])

In [21]:
#pull pricing data from 3 more BTC exchanges for better data integrity
exchanges = ['COINBASE','BITSTAMP','ITBIT']
exchange_data={} #initialise dictionary of all BTC exchanges
exchange_data['KRAKEN'] = btc_usd_price_kraken #add KRAKEN in dictionary
for exchange in exchanges:
    exchange_code = 'BCHARTS/{}USD'.format(exchange)
    btc_exchange_df = get_quandl_data(exchange_code)
    exchange_data[exchange] = btc_exchange_df

#merge all of pricing data into single df (combine common column):
def merge_dfs_on_column(dataframes,labels,col):
    """Merge a single column of each df into a new combined df"""
    series_dict={}
    for index in range(len(dataframes)):
        series_dict[labels[index]] = dataframes[index][col]
    return pd.DataFrame(series_dict)

#merge all columns on 'weighted price' column
btc_usd_datasets = merge_dfs_on_column(list(exchange_data.values()), list(exchange_data.keys()),'Weighted Price')

#preview last 5 rows to ensure data looks fine
btc_usd_datasets.tail()

Loaded BCHARTS/COINBASEUSD from cache. 
Loaded BCHARTS/BITSTAMPUSD from cache. 
Loaded BCHARTS/ITBITUSD from cache. 


BITSTAMP     COINBASE        ITBIT       KRAKEN
Date                                                          
2017-08-28  4290.845145  4313.550073  4307.521505  4296.631535
2017-08-29  4502.758977  4515.518693  4491.765244  4520.657103
2017-08-30  4564.263673  4579.991344  4568.021941  4576.087024
2017-08-31  4682.334106  4692.111552  4681.680593  4679.719705
2017-09-01  4805.955174  4823.283958  4814.454351  4809.634968

In [22]:
#visualise pricing datasets
def df_scatter(df,title,separate_y_axis=False,y_axis_label='',scale='linear',initial_hide=False):
    '''Generate a scatter plot of the entire df'''
    label_arr = list(df) #list the names of the column, in this case, the name of the exchange site
    series_arr = list(map(lambda col: df[col],label_arr))
    #map the lambda f(x)=df[col] on label_arr
    layout=go.Layout(title=title,
                    legend=dict(orientation='h'),
                    xaxis=dict(type='date'), #year 
                    yaxis=dict(title=y_axis_label, #empty space
                              showticklabels=not separate_y_axis, #True
                              type=scale
                    ) #this is default layout
    )
    
    y_axis_config = dict(overlaying='y', #creates small dictionary with overlaying : y, showticklabels : false, type : scale
                        showticklabels=False,
                        type=scale ) #type of data for the yaxis plot is a linear type
    
    visibility = 'visible'
    if initial_hide: #if True
        visibility = 'legendonly' #Determines whether or not this trace is visible.
    global trace_arr
    trace_arr = []
    for index,series in enumerate(series_arr):
        trace = go.Scatter(
                            x=series.index, #index of series_arr (the date) the left most column
                            y=series, #values of the series array
                            name=label_arr[index], #there are 4 BTC xchange sites, it will be named 1 of 4
                            visible = visibility
        )
        
        #add separate axis for the series (part of 'for loop')
        if separate_y_axis: #if True
            trace['yaxis'] = 'y{}'.format(index+1) #index from enumeration, index it like a dictionary bc it is, adding/declaring yaxis variable in trace to equal y1-4
            #if user wants serparate y axis then assign it y(n) to draw it (trace)
            layout['yaxis{}'.format(index+1)] = y_axis_config #assign yaxis1-4 as y_axis_config which was declared as small dictionary above
        trace_arr.append(trace)
    
    fig = go.Figure(data=trace_arr,layout=layout)
    py.iplot(fig)

In [23]:
#plot all of the BTC exchange prices
df_scatter(btc_usd_datasets,'Bitcoin Price (USD) By Exchange')


In [24]:
trace_arr

[{'name': 'BITSTAMP',
  'type': 'scatter',
  'visible': 'visible',
  'x': DatetimeIndex(['2011-09-13', '2011-09-14', '2011-09-15', '2011-09-16',
                 '2011-09-17', '2011-09-18', '2011-09-19', '2011-09-20',
                 '2011-09-21', '2011-09-22',
                 ...
                 '2017-08-23', '2017-08-24', '2017-08-25', '2017-08-26',
                 '2017-08-27', '2017-08-28', '2017-08-29', '2017-08-30',
                 '2017-08-31', '2017-09-01'],
                dtype='datetime64[ns]', name='Date', length=2181, freq='D'),
  'y': Date
  2011-09-13       5.929231
  2011-09-14       5.590798
  2011-09-15       5.094272
  2011-09-16       4.854515
  2011-09-17       4.870000
  2011-09-18       4.839576
  2011-09-19       4.900000
  2011-09-20       5.388054
  2011-09-21       5.706075
  2011-09-22       5.696960
  2011-09-23       5.707099
  2011-09-24       5.722494
  2011-09-25       6.050000
  2011-09-26       5.983073
  2011-09-27       4.895402
  2011-09-28   

In [25]:
import numpy as np

N = 1000
random_x = np.random.randn(N)
random_y = np.random.randn(N)

# Create a trace
trace = go.Scatter(
    x = random_x,
    y = random_y,
    mode = 'markers',
    #yaxis = 'y1'
)
trace['yaxis'] = 'y1' #name yaxis label this way or like above
data = [trace]

# Plot and embed in ipython notebook!
fig = go.Figure(data = data,layout = go.Layout(yaxis=dict(
        title=trace['yaxis'])))
py.iplot(fig, filename='basic-scatter')

In [26]:
#clean and remove zeros from df:
btc_usd_datasets.replace(0,np.nan, inplace=True) #inplace, make changes in place as it executes, replaces input with output,  (do not create a new object) 
df_scatter(btc_usd_datasets,'Bitcoin Price (USD) By Exchange')

In [27]:
#calculate the average BTC price as new column (new BT pricing index)
btc_usd_datasets['avg_btc_price_usd'] = btc_usd_datasets.mean(axis=1)

In [28]:
#plot the avg BTC price
btc_trace = go.Scatter(x=btc_usd_datasets.index, y=btc_usd_datasets['avg_btc_price_usd'])
py.iplot([btc_trace]) #needs to be a list

In [29]:
def get_json_data(json_url,cache_path):
    '''Download and cache JSON data, return as a df'''
    try:
        f = open(cache_path, 'rb') #read binary
        df = pickle.load(f)
        #Read a pickled object representation from the open file object file and 
        #return the reconstituted object hierarchy specified therein
        print('Loaded {} from cache'.format(json_url))
    except (OSError, IOError) as e: #IOError is only for windows, OSError = mistype, no data file, missing
        print('Downloading {}'.format(json_url))
        df = pd.read_json(json_url)
        df.to_pickle(cache_path)
        print('Cached {} at {}.format(json_url,cache_path')
    return df

#JSON format is text only, it can easily be sent to and from a server, and used 
#as a data format by any programming language. So, if you receive data from a server, 
#in JSON format, you can use it like any other JavaScript object

In [30]:
#Pickling - implements binary protocols for serializing and de-serializing a Python object structure.
#Pickling” is the process whereby a Python object hierarchy is converted into a byte stream, 
#and “unpickling” is the inverse operation, whereby a byte stream (from a binary file or bytes-like object) 
#is converted back into an object hierarchy

#differences bt JSON and pickle:
#=================================
#JSON is a text serialization format (it outputs unicode text, although most of the time it is 
#then encoded to utf-8), while pickle is a binary serialization format
#JSON is human-readable, while pickle is not;JSON is interoperable and widely used outside of 
#the Python ecosystem, while pickle is Python-specific
#JSON, by default, can only represent a subset of the Python built-in types, and no custom classes; 
#pickle can represent an extremely large number of Python types

#call our new get_json_data function to save the resulting data

base_polo_url = 'https://poloniex.com/public?command=returnChartData&currencyPair={}&start={}&end={}&period={}'
start_date = datetime.strptime('2015-01-01','%Y-%m-%d') #obtain data from start of 2015
#strptime() class method creates a datetime object from a string representing a date and time and a corresponding format string
end_date = datetime.now() #up until today
period = 86400 #pull daily data (86400 seconds /day)

def get_crypto_data(poloniex_pair): #polonix_pair will be the cache_path
    '''Retrieve cryptocurreny data from poloniex'''
    json_url = base_polo_url.format(poloniex_pair, start_date.timestamp(),end_date.timestamp(),period) 
    #timestamp() converts to POSIX standard that is a float value of the full date and time [Portable Operating System Interface] 
    data_df = get_json_data(json_url,poloniex_pair)
    data_df = data_df.set_index('date') #Set the DataFrame index (row labels) using one or more existing columns
    return data_df

#this function will take a cryptocurrency pair string (i.e. 'BTC_ETH') bitcoin & ethereum
#and return a df containing the historical excahnge rate of the 2 currencies

In [32]:
#Download tradign data from Poloniex:
#download exchange data for 9 top cryptocurrencies
#exchange to BTC since one must exchange to a cryptocurrency first before exchanging to USD

altcoins = ['ETH','LTC','XRP','ETC','STR','DASH','SC','XMR','XEM']
altcoin_data = {}
for altcoin in altcoins:
    coinpair = 'BTC_{}'.format(altcoin)
    crypto_price_df = get_crypto_data(coinpair)
    altcoin_data[altcoin] = crypto_price_df
    
#now we have a dictionary with 9 dfs each containing the historical daily
#avg exchange price bt the altcoin and BTC

#test using Ethereum

altcoin_data['ETH'].tail()

URLError: <urlopen error [SSL: CERTIFICATE_VERIFY_FAILED] certificate verify failed (_ssl.c:748)>

In [ ]:
#convert prices to USD
#calculate the historical USD values for each altcoin using our BTC pricing index

#calculate USD price as a new column in each altcoin df:
for altcoin in altcoin_data.keys():
    altcoin_data[altcoin]['price_usd'] = altcoin_data[altcoin]['weightedAverage']*btc_usd_datasets['avg_btc_price_usd']

In [15]:
#use mer_dfs_on_column function to create a combined df of the USD price
combined_df = merge_dfs_on_column(list(altcoin_data.values()),list(altcoin_data.keys()),'price_usd') #column = price_usd

#also combine BTC prices as a final column to the combined DF
combined_df['BTC'] = btc_usd_datasets['avg_btc_price_usd']

#single df containing daily USD prices for 10 cryptocurrencies

In [13]:
#scatter plot all 10 cryptocurrencies
df_scatter(combined_df,'Cryptocurrency Prices (USD)',separate_y_axis=False,y_axis_label='Coin Value (USD)',scale='log')

In [14]:
df_scatter(combined_df,'Cryptocurrency Prices (USD)',separate_y_axis=False,y_axis_label='Coin Value (USD)',scale='linear')

In [ ]:
#perform correlation analysis:
#the exchange rates seem slighly correlated across whole market, markedly around Apr 2017
#Pearson correlation coefficient for each column in the dataframe against each other column
#use the daily return percentages instead of the absolute price values in calculating the correlation coefficients

#convert each cell in the dataframe from an absolute price value to a daily return percentage
#bc computing correlations directly on a non-stationary time series will result in biased results

# Calculate the pearson correlation coefficients for cryptocurrencies in 2016
combined_df_2016 = combined_df[combined_df.index.year == 2016]
combined_df_2016.pct_change().corr(method='pearson')
#pd.Series.pct_change(periods=1,fill_method='pad',limit=None,freq=None) - percent change over given number of periods
#under the bonnet: .pct_change() does:
#returns = (df[col1][1] - df[col1][1].shift(1))/df[col1][1], where shift(1) shifts a column over 1

In [15]:
combined_df

DASH        ETC         ETH        LTC        SC       STR  \
date                                                                           
2015-01-02    1.974292        NaN         NaN   2.685418       NaN  0.005536   
2015-01-03    1.818238        NaN         NaN   2.389670       NaN  0.005117   
2015-01-04    1.705425        NaN         NaN   2.079496       NaN  0.004521   
2015-01-05    1.650610        NaN         NaN   2.076988       NaN  0.004870   
2015-01-06    1.667679        NaN         NaN   2.091707       NaN  0.004928   
2015-01-07    1.742234        NaN         NaN   2.183424       NaN  0.005164   
2015-01-08    1.730026        NaN         NaN   2.099834       NaN  0.005563   
2015-01-09    1.747407        NaN         NaN   2.051141       NaN  0.005792   
2015-01-10    1.711341        NaN         NaN   1.801965       NaN  0.005455   
2015-01-11    1.647092        NaN         NaN   1.777432       NaN  0.005094   
2015-01-12    1.674630        NaN         NaN   1.796554       NaN  0.005038   
2015-01-13    1.440859        NaN         NaN   1.567368       NaN  0.004310   
2015-01-14    1.179139        NaN         NaN   1.362779       NaN  0.004223   
2015-01-15    1.273059        NaN         NaN   1.346519       NaN  0.005000   
2015-01-16    1.303848        NaN         NaN   1.423123       NaN  0.004664   
2015-01-17    1.174390        NaN         NaN   1.356784       NaN  0.004560   
2015-01-18    1.301325        NaN         NaN   1.342925       NaN  0.004878   
2015-01-19    1.326747        NaN         NaN   1.336845       NaN  0.005049   
2015-01-20    1.409598        NaN         NaN   1.366350       NaN  0.004852   
2015-01-21    1.547142        NaN         NaN   1.361731       NaN  0.004996   
2015-01-22    1.648366        NaN         NaN   1.452261       NaN  0.005112   
2015-01-23    1.617673        NaN         NaN   1.436409       NaN  0.004829   
2015-01-24    1.677723        NaN         NaN   1.747393       NaN  0.004956   
2015-01-25    1.777200        NaN         NaN   2.187072       NaN  0.004830   
2015-01-26    1.940932        NaN         NaN   2.286462       NaN  0.004702   
2015-01-27    1.714437        NaN         NaN   2.001324       NaN  0.004266   
2015-01-28    1.788605        NaN         NaN   2.074580       NaN  0.004328   
2015-01-29    1.621902        NaN         NaN   1.928742       NaN  0.004146   
2015-01-30    1.587644        NaN         NaN   1.916548       NaN  0.004250   
2015-01-31    1.662746        NaN         NaN   1.961243       NaN  0.004121   
...                ...        ...         ...        ...       ...       ...   
2017-08-08  198.362040  15.471647  286.243466  46.697246  0.009371  0.022368   
2017-08-09  199.681855  15.667252  299.191073  48.255836  0.009304  0.023209   
2017-08-10  201.349579  15.405582  301.902369  47.624440  0.008716  0.022810   
2017-08-11  203.675501  15.246134  301.155217  46.855315  0.008117  0.021493   
2017-08-12  213.272610  15.526505  325.266338  48.286904  0.008682  0.022581   
2017-08-13  197.996553  14.177236  290.464676  45.683989  0.007365  0.018554   
2017-08-14  205.017216  14.586916  309.965714  46.912408  0.007159  0.018908   
2017-08-15  197.380858  13.364269  284.056792  43.192665  0.007594  0.017459   
2017-08-16  219.226011  13.778619  295.712624  43.592051  0.007670  0.017938   
2017-08-17  244.420394  13.853209  303.140033  43.814792  0.007202  0.017484   
2017-08-18  228.259855  13.600717  296.398352  45.274621  0.006854  0.016927   
2017-08-19  282.494850  13.537773  291.070974  44.708885  0.006276  0.016097   
2017-08-20  300.185832  13.644978  293.065362  45.526405  0.007245  0.017520   
2017-08-21  284.238685  14.202012  323.736975  46.654474  0.006995  0.018332   
2017-08-22  283.392362  14.051829  312.694691  46.002557  0.006555  0.019120   
2017-08-23  293.277159  15.499278  319.711922  52.099427  0.007023  0.022564   
2017-08-24  300.624092  15.475337  322.404172  51.698642  0.007126  0.020071   
2017-08-25  314.52